# FinBert

## Sources

[HugginFace](https://huggingface.co/ProsusAI/finbert)
[Tutorial](https://medium.com/codex/stocks-news-sentiment-analysis-with-deep-learning-transformers-and-machine-learning-cdcdb827fc06)

In [13]:
!pip install transformers tqdm pandas numpy torch torchvision torchaudio pip -Uq

ERROR: To modify pip, please run the following command:
C:\Users\phhor\PycharmProjects\aki_prj23_transparenzregister\venv\Scripts\python.exe -m pip install transformers tqdm pandas numpy torch torchvision torchaudio pip -Uq

[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [16]:
import pandas as pd
from transformers import AutoTokenizer, AutoModelForSequenceClassification

# create a tokenizer object
tokenizer = AutoTokenizer.from_pretrained("ProsusAI/finbert")

# fetch the pretrained model
model = AutoModelForSequenceClassification.from_pretrained("ProsusAI/finbert")

In [12]:
# A headline to be used as input
import torch

headline = "Microsoft fails to hit profit expectations"
headline2 = (
    "Am Aktienmarkt überwieg weiter die Zuversicht, wie der Kursverlauf des DAX zeigt."
)

# Pre-process input phrase
input_tokens = tokenizer(headline2, padding=True, truncation=True, return_tensors="pt")
# Run inference on the tokenized phrase
output = model(**input_tokens)

# Pass model output logits through a softmax layer.
sentim_scores = torch.nn.functional.softmax(output.logits, dim=-1)
sentim_scores

tensor([[0.0535, 0.0279, 0.9185]], grad_fn=<SoftmaxBackward0>)

In [56]:
def analyze_sentiment(text: str):
    print(text)
    input_tokens = tokenizer(text, padding=True, truncation=True, return_tensors="pt")
    output = model(**input_tokens)
    return pd.Series(
        torch.nn.functional.softmax(output.logits, dim=-1)[0].data,
        index=["+", "0", "-"],
    )


tf = analyze_sentiment(headline)
tf

Microsoft fails to hit profit expectations


+    0.034084
0    0.932933
-    0.032982
dtype: float32

In [69]:
text_df = pd.DataFrame(
    [
        {"text": "Microsoft fails to hit profit expectations", "lan": "en"},
        {
            "text": "Am Aktienmarkt überwieg weiter die Zuversicht, wie der Kursverlauf des DAX zeigt.",
            "lan": "de",
        },
        {"text": "Stocks rallied and the British pound gained.", "lan": "en"},
        {
            "text": "Meyer Burger bedient ab sofort australischen Markt und präsentiert sich auf Smart Energy Expo in Sydney.",
            "lan": "de",
        },
    ]
)
text_df

text lan
0         Microsoft fails to hit profit expectations  en
1  Am Aktienmarkt überwieg weiter die Zuversicht,...  de
2       Stocks rallied and the British pound gained.  en
3  Meyer Burger bedient ab sofort australischen M...  de

In [71]:
def analyse_sentiments(texts: pd.Series) -> pd.DataFrame:
    values = texts["text"].apply(analyze_sentiment)
    # print(values)
    texts[["+", "0", "-"]] = values
    return texts


analyse_sentiments(text_df)

Microsoft fails to hit profit expectations
Am Aktienmarkt überwieg weiter die Zuversicht, wie der Kursverlauf des DAX zeigt.
Stocks rallied and the British pound gained.
Meyer Burger bedient ab sofort australischen Markt und präsentiert sich auf Smart Energy Expo in Sydney.


text lan         +         0   
0         Microsoft fails to hit profit expectations  en  0.034084  0.932933  \
1  Am Aktienmarkt überwieg weiter die Zuversicht,...  de  0.053528  0.027950   
2       Stocks rallied and the British pound gained.  en  0.898361  0.034474   
3  Meyer Burger bedient ab sofort australischen M...  de  0.116597  0.012790   

          -  
0  0.032982  
1  0.918522  
2  0.067165  
3  0.870613